In [1]:
pip install ydata-profiling


[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
pip install tensorflow

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [3]:
pip install xgboost

Note: you may need to restart the kernel to use updated packages.Requirement already satisfied: xgboost in c:\users\hp\anaconda3\lib\site-packages (3.0.0)




[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [4]:
import pandas as pd          # For handling data
import numpy as np           # For numerical operations
import matplotlib.pyplot as plt  # For plotting (optional, for visualization)
from sklearn.model_selection import train_test_split  # For splitting data
from sklearn.metrics import mean_squared_error, r2_score  # For evaluation
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler
from ydata_profiling import ProfileReport
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Input, LSTM, Dropout, Dense
from tensorflow.keras.callbacks import EarlyStopping
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import classification_report, confusion_matrix
from xgboost import XGBClassifier
from sklearn.ensemble import RandomForestClassifier

In [5]:
df = pd.read_excel(r"C:\Users\HP\OneDrive\Pictures\Water disease Cleaned Dataset.xlsx")
df

Date  Month      Region  Region Code Community   Country  \
0     2019-01-01      1  Urban Slum            5    Makoko   Nigeria   
1     2019-01-01      1  Peri-Urban            3   Entebbe    Uganda   
2     2019-01-01      1  Urban Slum            5   Mathare     Kenya   
3     2019-01-01      1  Urban Slum            5    Kibera     Kenya   
4     2019-01-01      1     Dryland            2    Maradi     Niger   
...          ...    ...         ...          ...       ...       ...   
10395 2023-12-22     12       Rural            4     Nzega  Tanzania   
10396 2023-12-22     12       Rural            4     Nzega  Tanzania   
10397 2023-12-22     12  Peri-Urban            3     Kasoa     Ghana   
10398 2023-12-22     12       Rural            4     Nzega  Tanzania   
10399 2023-12-22     12       Rural            4     Nzega  Tanzania   

       Turbidity(NTU)  Ecoli_Count(CFU/100ml)  Nitrate(mg/L)    pH  \
0                5.75                      97          23.24  7.26   
1                4.12                      55          13.77  6.69   
2                2.40                      72          24.97  6.51   
3                4.49                     110          19.52  6.50   
4               10.39                      95          19.80  6.73   
...               ...                     ...            ...   ...   
10395            2.40                      29           6.68  7.08   
10396            4.56                      31           3.63  6.95   
10397            1.82                      53          14.42  7.09   
10398            2.58                       0           8.54  7.11   
10399            0.80                      22          17.38  7.08   

       Cholera_Cases  Typhoid_Cases  Diarrhea_Cases  Total Waterborne Cases  \
0                  2              3               4                       9   
1                  0              3               5                       8   
2                  5              2               2                       9   
3                  4              3               3                      10   
4                  8              3               3                      14   
...              ...            ...             ...                     ...   
10395              0              1               0                       1   
10396              3              1               2                       6   
10397              6              3               2                      11   
10398              0              0               0                       0   
10399              2              0               1                       3   

      Risk Level  
0         Medium  
1         Medium  
2         Medium  
3           High  
4           High  
...          ...  
10395        Low  
10396     Medium  
10397       High  
10398        Low  
10399        Low  

[10400 rows x 15 columns]

### Data Preparation

In [7]:
# profiling

profile = ProfileReport(df, explorative=True)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [8]:
# Check if the 'Date' column is sorted (ignoring missing values)
df['Date'].dropna().is_monotonic_increasing


True

In [9]:
df['Date'] = pd.to_datetime(df['Date'], errors='coerce')
df = df.sort_values(by='Date')

In [10]:
# Extract the month from the 'Date' column
df['Month'] = df['Date'].dt.month

# Now ffill can be applied to both 'Date' and 'Month'
df[['Date', 'Month']] = df[['Date', 'Month']].ffill()

In [11]:
df = df.reset_index(drop=True)


In [12]:
# Save to a new Excel file
df.to_excel(r"C:\Users\HP\OneDrive\Pictures\Water disease Cleaned Dataset.xlsx", index=False)

In [13]:
df

Date  Month      Region  Region Code Community   Country  \
0     2019-01-01      1  Urban Slum            5    Makoko   Nigeria   
1     2019-01-01      1     Coastal            1  Bagamoyo  Tanzania   
2     2019-01-01      1     Coastal            1     Bonny   Nigeria   
3     2019-01-01      1       Rural            4  Chibombo    Zambia   
4     2019-01-01      1  Peri-Urban            3   Ikorodu   Nigeria   
...          ...    ...         ...          ...       ...       ...   
10395 2023-12-22     12  Peri-Urban            3    Nsawam     Ghana   
10396 2023-12-22     12  Peri-Urban            3    Nsawam     Ghana   
10397 2023-12-22     12     Coastal            1  Bagamoyo  Tanzania   
10398 2023-12-22     12  Peri-Urban            3    Nsawam     Ghana   
10399 2023-12-22     12       Rural            4     Nzega  Tanzania   

       Turbidity(NTU)  Ecoli_Count(CFU/100ml)  Nitrate(mg/L)    pH  \
0                5.75                      97          23.24  7.26   
1                5.19                     101          20.53  6.36   
2                3.98                      57          14.90  7.23   
3                0.84                       0          17.42  6.78   
4                2.97                      42           9.41  6.86   
...               ...                     ...            ...   ...   
10395            1.58                      39          15.43  6.74   
10396            1.37                      36          12.63  6.54   
10397            5.17                     115          16.44  6.47   
10398            6.36                      91          16.46  6.97   
10399            0.80                      22          17.38  7.08   

       Cholera_Cases  Typhoid_Cases  Diarrhea_Cases  Total Waterborne Cases  \
0                  2              3               4                       9   
1                  4              5               6                      15   
2                  6              3               5                      14   
3                  0              0               0                       0   
4                  7              1               5                      13   
...              ...            ...             ...                     ...   
10395              4              0               2                       6   
10396              2              2               1                       5   
10397              8              1               8                      17   
10398              8              4               3                      15   
10399              2              0               1                       3   

      Risk Level  
0         Medium  
1           High  
2           High  
3            Low  
4           High  
...          ...  
10395     Medium  
10396     Medium  
10397       High  
10398       High  
10399        Low  

[10400 rows x 15 columns]

In [14]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10400 entries, 0 to 10399
Data columns (total 15 columns):
 #   Column                  Non-Null Count  Dtype         
---  ------                  --------------  -----         
 0   Date                    10400 non-null  datetime64[ns]
 1   Month                   10400 non-null  int32         
 2   Region                  10400 non-null  object        
 3   Region Code             10400 non-null  int64         
 4   Community               10400 non-null  object        
 5   Country                 10400 non-null  object        
 6   Turbidity(NTU)          10400 non-null  float64       
 7   Ecoli_Count(CFU/100ml)  10400 non-null  int64         
 8   Nitrate(mg/L)           10400 non-null  float64       
 9   pH                      10400 non-null  float64       
 10  Cholera_Cases           10400 non-null  int64         
 11  Typhoid_Cases           10400 non-null  int64         
 12  Diarrhea_Cases          10400 non-null  int64 

In [15]:
df.isna().sum()

Date                      0
Month                     0
Region                    0
Region Code               0
Community                 0
Country                   0
Turbidity(NTU)            0
Ecoli_Count(CFU/100ml)    0
Nitrate(mg/L)             0
pH                        0
Cholera_Cases             0
Typhoid_Cases             0
Diarrhea_Cases            0
Total Waterborne Cases    0
Risk Level                0
dtype: int64

### LINEAR REGRESSION

In [17]:
# Select features and target
features = ['Turbidity(NTU)', 'Ecoli_Count(CFU/100ml)', 'Nitrate(mg/L)', 'pH']
target = 'Total Waterborne Cases'

In [18]:
X = df[features]
y = df[target]
X
y

0         9
1        15
2        14
3         0
4        13
         ..
10395     6
10396     5
10397    17
10398    15
10399     3
Name: Total Waterborne Cases, Length: 10400, dtype: int64

In [19]:
# Split data into train and test sets (80% train, 20% test)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [20]:
# Train the model
model = LinearRegression()
model.fit(X_train, y_train)

LinearRegression()

In [21]:
# Make predictions
y_pred = model.predict(X_test)


In [22]:
import numpy as np
import pandas as pd

# y_test = actual values
# y_pred = predictions from your model

residuals = y_test - y_pred
residuals_df = pd.DataFrame({
    'Actual': y_test,
    'Predicted': y_pred,
    'Residuals': residuals
})

# Set threshold for outliers (e.g., 3 standard deviations)
std_dev = residuals.std()
threshold = 3 * std_dev

outliers = residuals_df[np.abs(residuals_df['Residuals']) > threshold]
print(outliers)


      Actual  Predicted  Residuals
6743      27  14.042387  12.957613
373        6  18.067779 -12.067779
6388      27  15.634231  11.365769
3578      24  13.874622  10.125378
5836      30  17.378002  12.621998
8928      10  20.304230 -10.304230
217        4  14.337758 -10.337758
3282      30  17.360838  12.639162
7243      25  13.578334  11.421666


In [23]:
# Evaluate the model
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print("Mean Squared Error (MSE):", mse)
print("R² Score:", r2)

Mean Squared Error (MSE): 10.996453062235528
R² Score: 0.6938622535869488


In [24]:
print(X_train.shape, X_test.shape)
print(y_train.shape, y_test.shape)


(8320, 4) (2080, 4)
(8320,) (2080,)


In [25]:
import pandas as pd
from sklearn.linear_model import LinearRegression

lr = LinearRegression()
lr.fit(X, y)
pred = lr.predict(X)

if np.allclose(pred, y):
    print("Target is a perfect combination of features.")
    coefs = pd.Series(lr.coef_, index=X.columns)
    print("Coefficients:\n", coefs)
    print("Intercept:", lr.intercept_)


### RANDOMFORESTREGRESSOR

In [27]:
# Select features and target
features = ['Turbidity(NTU)', 'Ecoli_Count(CFU/100ml)', 'Nitrate(mg/L)', 'pH']
target = 'Total Waterborne Cases'

X = df[features]
y = df[target]

# Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Train Random Forest Regressor
rf_model = RandomForestRegressor(n_estimators=100, random_state=42)
rf_model.fit(X_train, y_train)

RandomForestRegressor(random_state=42)

In [28]:
# Predict
y_pred = rf_model.predict(X_test)


In [29]:
# Evaluate
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print("Random Forest MSE:", mse)
print("Random Forest R² Score:", r2)


Random Forest MSE: 12.408022740384617
Random Forest R² Score: 0.6545646039059245


### XGBREGRESSOR

In [31]:
# Features and target
features = ['Turbidity(NTU)', 'Ecoli_Count(CFU/100ml)', 'Nitrate(mg/L)', 'pH']
target = 'Total Waterborne Cases'

X = df[features]
y = df[target]

# Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Train XGBoost Regressor
xgb_model = XGBRegressor(n_estimators=100, learning_rate=0.1, random_state=42)
xgb_model.fit(X_train, y_train)



XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.1, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=None,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=100,
             n_jobs=None, num_parallel_tree=None, ...)

In [32]:
# Predict
y_pred = xgb_model.predict(X_test)

In [33]:
# Evaluate
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print("XGBoost MSE:", mse)
print("XGBoost R² Score:", r2)


XGBoost MSE: 11.72702407836914
XGBoost R² Score: 0.6735233664512634


### LSTM

In [35]:
print(X_train.shape)


(8320, 4)


In [36]:
print(X_train.shape)               # Should show (8320, 7)
print(X_train.size)                # Should be 58240


(8320, 4)
33280


In [37]:
# Reshape for models like LSTM
X_train_reshaped = X_train.values.reshape((X_train.shape[0], 1, X_train.shape[1]))
X_test_reshaped = X_test.values.reshape((X_test.shape[0], 1, X_test.shape[1]))


In [38]:
model = Sequential([
    Input(shape=(1, X_train.shape[1])),  # Now it's (timesteps=1, features=n)
    LSTM(64, return_sequences=False),
    Dropout(0.2),
    Dense(1)
])


In [39]:
scaler_y = MinMaxScaler()
scaler_y.fit(y_train.values.reshape(-1, 1))


MinMaxScaler()

In [40]:
# Ensure X_test is a NumPy array
if isinstance(X_test, pd.DataFrame) or isinstance(X_test, pd.Series):
    X_test = X_test.to_numpy()

# If 1D, reshape to (n_samples, 1, 1)
if X_test.ndim == 1:
    X_test = X_test.reshape(-1, 1, 1)
# If 2D, reshape to (n_samples, 1, n_features)
elif X_test.ndim == 2:
    X_test = X_test.reshape((X_test.shape[0], 1, X_test.shape[1]))


In [41]:
# Assuming y_test is the actual test set target values
y_test_actual = y_test

# Now you can proceed with the evaluation
mse = mean_squared_error(y_test_actual, y_pred)
r2 = r2_score(y_test_actual, y_pred)

# If you used a scaler, you may need to inverse transform the predictions and actual values
# Example: Inverse transform if you used a scaler on y values
# y_test_actual = scaler_y.inverse_transform(y_test.reshape(-1, 1))


In [42]:
# Convert Series to NumPy array before reshaping
y_test_actual = scaler_y.inverse_transform(y_test.values.reshape(-1, 1))
y_pred_actual = scaler_y.inverse_transform(y_pred.reshape(-1, 1))


In [43]:
mse = mean_squared_error(y_test_actual, y_pred_actual)
r2 = r2_score(y_test_actual, y_pred_actual)

print("Mean Squared Error (MSE):", mse)
print("R-squared (R²) Score:", r2)


Mean Squared Error (MSE): 17836.80322639064
R-squared (R²) Score: 0.6735233967445887


### LOGISTICREGRESSION

In [45]:
# Select features and target
features = ['Turbidity(NTU)', 'Ecoli_Count(CFU/100ml)', 'Nitrate(mg/L)', 'pH']
target = 'Risk Level'


In [46]:
X = df[features]
y = df[target]

In [47]:
# Encode categorical target
le = LabelEncoder()
y_encoded = le.fit_transform(y)

In [48]:
# Split data
X_train, X_test, y_train, y_test = train_test_split(X, y_encoded, test_size=0.2, random_state=42)

In [49]:
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

model = LogisticRegression(max_iter=500)
model.fit(X_scaled, y)


LogisticRegression(max_iter=500)

In [50]:
# Predictmodel = LogisticRegression(max_iter=1000)
model.fit(X_train, y_train)         # X_train should be a DataFrame
y_pred = model.predict(X_test)      # X_test should be a DataFrame

y_pred = model.predict(X_test)

In [51]:
# Generate classification report as a dictionary
report = classification_report(y_test, y_pred, output_dict=True, zero_division=0)

# Now print summary metrics
print("✅ Overall Accuracy:", round(report["accuracy"], 2))
print("✅ Macro Avg F1-score:", round(report["macro avg"]["f1-score"], 2))
print("✅ Weighted Avg F1-score:", round(report["weighted avg"]["f1-score"], 2))


✅ Overall Accuracy: 0.78
✅ Macro Avg F1-score: 0.72
✅ Weighted Avg F1-score: 0.77


### RANDOMFORESTCLASSIFIER

In [53]:
# Select features and target
features = ['Turbidity(NTU)', 'Ecoli_Count(CFU/100ml)', 'Nitrate(mg/L)', 'pH']
target = ['Risk Level']

X = df[features]
y = df[target]

In [54]:
# Target
y = df['Risk Level']  # 1D target column

# Encode class labels
le = LabelEncoder()
y_encoded = le.fit_transform(y)  # No warning now

# Continue with train_test_split


In [55]:
# Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y_encoded, test_size=0.2, random_state=42)

In [56]:
# Train the Random Forest Classifier
rf_model = RandomForestClassifier(n_estimators=100, random_state=42)
rf_model.fit(X_train, y_train)

RandomForestClassifier(random_state=42)

In [57]:
# Predict
y_pred = rf_model.predict(X_test)

In [58]:
# Evaluate
print("Classification Report:\n", classification_report(y_test, y_pred, target_names=le.classes_))
print("Confusion Matrix:\n", confusion_matrix(y_test, y_pred))

Classification Report:
               precision    recall  f1-score   support

        High       0.83      0.89      0.86      1230
         Low       0.75      0.67      0.71       305
      Medium       0.56      0.51      0.53       545

    accuracy                           0.76      2080
   macro avg       0.72      0.69      0.70      2080
weighted avg       0.75      0.76      0.75      2080

Confusion Matrix:
 [[1100    6  124]
 [  11  203   91]
 [ 209   60  276]]


### XGBCLASSIFIER

In [60]:
# STEP 2: Prepare features and encoded labels
features = ['Turbidity(NTU)', 'Ecoli_Count(CFU/100ml)', 'Nitrate(mg/L)', 'pH']
X = df[features]
y = df['Risk Level']

le = LabelEncoder()
y_encoded = le.fit_transform(y)  # Convert to 0, 1, 2

In [61]:
# STEP 3: Split data
X_train, X_test, y_train, y_test = train_test_split(X, y_encoded, test_size=0.2, random_state=42)

In [62]:
# STEP 4: Train XGBoost Classifier
model = XGBClassifier(eval_metric='mlogloss', random_state=42)
model.fit(X_train, y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric='mlogloss',
              feature_types=None, feature_weights=None, gamma=None,
              grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=None, n_jobs=None,
              num_parallel_tree=None, ...)

In [131]:
# STEP 5: Predict and evaluate
y_pred = model.predict(X_test)

print("Classification Report:\n", classification_report(y_test, y_pred, target_names=le.classes_))
print("Confusion Matrix:\n", confusion_matrix(y_test, y_pred))


Classification Report:
               precision    recall  f1-score   support

        High       0.84      0.90      0.87      1230
         Low       0.76      0.65      0.70       305
      Medium       0.56      0.52      0.54       545

    accuracy                           0.76      2080
   macro avg       0.72      0.69      0.70      2080
weighted avg       0.76      0.76      0.76      2080

Confusion Matrix:
 [[1104    3  123]
 [   9  198   98]
 [ 199   60  286]]


In [135]:
# Save to a new Excel file
df.to_excel(r"C:\Users\HP\OneDrive\Pictures\Water disease Cleaned Dataset.xlsx", index=False)


In [136]:
# Save to CSV instead of Excel
df.to_csv(r"C:\Users\HP\OneDrive\Pictures\Water_disease_Cleaned_Dataset.csv", index=False, encoding="utf-8")


In [139]:
# Reload and check first few rows
check_df = pd.read_csv(r"C:\Users\HP\OneDrive\Pictures\Water_disease_Cleaned_Dataset.csv")
check_df.head()


Date  Month      Region  Region Code Community   Country  \
0  2019-01-01      1  Urban Slum            5    Makoko   Nigeria   
1  2019-01-01      1     Coastal            1  Bagamoyo  Tanzania   
2  2019-01-01      1     Coastal            1     Bonny   Nigeria   
3  2019-01-01      1       Rural            4  Chibombo    Zambia   
4  2019-01-01      1  Peri-Urban            3   Ikorodu   Nigeria   

   Turbidity(NTU)  Ecoli_Count(CFU/100ml)  Nitrate(mg/L)    pH  Cholera_Cases  \
0            5.75                      97          23.24  7.26              2   
1            5.19                     101          20.53  6.36              4   
2            3.98                      57          14.90  7.23              6   
3            0.84                       0          17.42  6.78              0   
4            2.97                      42           9.41  6.86              7   

   Typhoid_Cases  Diarrhea_Cases  Total Waterborne Cases Risk Level  
0              3               4                       9     Medium  
1              5               6                      15       High  
2              3               5                      14       High  
3              0               0                       0        Low  
4              1               5                      13       High

In [141]:
df.to_csv(r"C:\Users\HP\Downloads\Water_disease_Cleaned_Dataset.csv", index=False, encoding="utf-8")


In [164]:
import pandas as pd
import smtplib
from email.mime.multipart import MIMEMultipart
from email.mime.text import MIMEText
from datetime import datetime

In [165]:
# === CONFIGURATION ===
CSV_PATH = r"C:\Users\HP\Downloads\Water_disease_Cleaned_Dataset.csv"  
RISK_COLUMN = "Risk Level"  # Column containing High/Medium/Low labels

# Email settings
SENDER_EMAIL = "da14@gmail.com"
SENDER_PASSWORD = "DataVerseAfrica" 
RECEIVER_EMAIL = "healthcarebody@example.com"
SMTP_SERVER = "smtp.gmail.com"
SMTP_PORT = 587

# === LOAD & FILTER DATA ===
df = pd.read_csv(CSV_PATH)
df

Date  Month      Region  Region Code Community   Country  \
0      2019-01-01      1  Urban Slum            5    Makoko   Nigeria   
1      2019-01-01      1     Coastal            1  Bagamoyo  Tanzania   
2      2019-01-01      1     Coastal            1     Bonny   Nigeria   
3      2019-01-01      1       Rural            4  Chibombo    Zambia   
4      2019-01-01      1  Peri-Urban            3   Ikorodu   Nigeria   
...           ...    ...         ...          ...       ...       ...   
10395  2023-12-22     12  Peri-Urban            3    Nsawam     Ghana   
10396  2023-12-22     12  Peri-Urban            3    Nsawam     Ghana   
10397  2023-12-22     12     Coastal            1  Bagamoyo  Tanzania   
10398  2023-12-22     12  Peri-Urban            3    Nsawam     Ghana   
10399  2023-12-22     12       Rural            4     Nzega  Tanzania   

       Turbidity(NTU)  Ecoli_Count(CFU/100ml)  Nitrate(mg/L)    pH  \
0                5.75                      97          23.24  7.26   
1                5.19                     101          20.53  6.36   
2                3.98                      57          14.90  7.23   
3                0.84                       0          17.42  6.78   
4                2.97                      42           9.41  6.86   
...               ...                     ...            ...   ...   
10395            1.58                      39          15.43  6.74   
10396            1.37                      36          12.63  6.54   
10397            5.17                     115          16.44  6.47   
10398            6.36                      91          16.46  6.97   
10399            0.80                      22          17.38  7.08   

       Cholera_Cases  Typhoid_Cases  Diarrhea_Cases  Total Waterborne Cases  \
0                  2              3               4                       9   
1                  4              5               6                      15   
2                  6              3               5                      14   
3                  0              0               0                       0   
4                  7              1               5                      13   
...              ...            ...             ...                     ...   
10395              4              0               2                       6   
10396              2              2               1                       5   
10397              8              1               8                      17   
10398              8              4               3                      15   
10399              2              0               1                       3   

      Risk Level  
0         Medium  
1           High  
2           High  
3            Low  
4           High  
...          ...  
10395     Medium  
10396     Medium  
10397       High  
10398       High  
10399        Low  

[10400 rows x 15 columns]

In [166]:
# Filter for High and Medium risks
filtered_df = df[df[RISK_COLUMN].isin(["High", "Medium"])]

# Create a daily summary
summary = filtered_df.groupby(RISK_COLUMN).size().reset_index(name="Count")
print(summary)


  Risk Level  Count
0       High   6096
1     Medium   2801


In [167]:
# Convert to HTML table for email
summary_html = summary.to_html(index=False)

# === EMAIL CONTENT ===
today = datetime.now().strftime("%Y-%m-%d")
subject = f"Daily Risk Summary - {today}"
body = f"""
Hello Healthcare Team,<br><br>
Here is the summary of today's high and medium risk cases:<br><br>
{summary_html}
<br><br>
Stay safe,<br>
Automated Notifier
"""

# === SEND EMAIL ===
try:
    msg = MIMEMultipart()
    msg["From"] = SENDER_EMAIL
    msg["To"] = RECEIVER_EMAIL
    msg["Subject"] = subject
    msg.attach(MIMEText(body, "html"))

    server = smtplib.SMTP("smtp.gmail.com", 587)
    server.starttls()
    server.login("da14@gmail.com", "DataVerseAfrica")
    server.sendmail(
        "da14@gmail.com",
        "smtp.gmail.com",
        "Subject: Test Email\n\nThis is a test email."
    )
    server.quit()
    print("✅ Email sent successfully!")
except Exception as e:
    print(f"❌ Failed to send email: {e}")

❌ Failed to send email: [WinError 10060] A connection attempt failed because the connected party did not properly respond after a period of time, or established connection failed because connected host has failed to respond
